# Incremental/Online Training with Scikit-learn and Production with Skops
In this tutorial, we will train online learning models with Scikit-learn, look at differences between warm and cold start and use skops to improve reproducibility!

In [1]:
!pip install datasets
!pip install skops

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.8/58.8 kB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 182.4/182.4 kB 7.4 MB/s eta 0:00:00
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.7.0
    Uninstalling huggingface-hub-0.7.0:
      Successfully uninstalled huggingface-hub-0.7.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cached-path 1.1.3 requires huggingface-hub<0.8.0,>=0.0.12, but you have huggingface-hub 0.11.1 which is incompatible.


In [2]:
import pandas as pd
import datasets
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.ensemble import HistGradientBoostingRegressor
import sklearn.neural_network
import numpy as np

In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

We will use a dataset from datasets library.

In [4]:
dataset = datasets.load_dataset("scikit-learn/auto-mpg")
df = pd.DataFrame(dataset["train"])

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/csv/scikit-learn--auto-mpg-a20aa45e3b31b7e3/0.0.0/433e0ccc46f9880962cc2b12065189766fbb2bee57a221866138fb9203c83519. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

# Preprocessing data

In [5]:
df.head()

mpg  cylinders  displacement horsepower  weight  acceleration  model year  \
0  18.0          8         307.0        130    3504          12.0          70   
1  15.0          8         350.0        165    3693          11.5          70   
2  18.0          8         318.0        150    3436          11.0          70   
3  16.0          8         304.0        150    3433          12.0          70   
4  17.0          8         302.0        140    3449          10.5          70   

   origin                   car name  
0       1  chevrolet chevelle malibu  
1       1          buick skylark 320  
2       1         plymouth satellite  
3       1              amc rebel sst  
4       1                ford torino

In [6]:
df.drop("car name", inplace = True, axis = 1)
df.drop(df[df.horsepower == "?"].index, inplace=True)

In [7]:
y = df["mpg"]
X = df.loc[:, df.columns != "mpg"]
X_train, X_test, y_train, y_test = train_test_split(X, y)

## Model Training

Scikit-learn provides couple of model training procedures. In this notebook, we'll go through partial_fit and neural networks with warm and cold starts. What partial_fit does is that it enables you to keep fitting the model on new data, lets you come up with a better fit that is adapted to recent data, technically better for data drifts. However, to my opinion, given it's super easy and fast to fit models in scikit-learn, it's always better to fit the model instead of partial_fit. You can also set warm_start to True if you want to not reset the trainable parameters and make use of them, however, it doesn't really work much for fit, it adjusts lightly in partial_fit. 

See more in references section of this notebook.

## Warm Start vs Cold Start
Difference between warm and cold starts (namely, warm_start parameter being True or False) is that one resets the trainable parameters for next run.

We'll fit two models with cold starts, note below how the parameters change after fitting (simply because everything's reset before fit)

In [8]:
np.random.seed(0)

cold_model = sklearn.neural_network.MLPRegressor(hidden_layer_sizes=(), warm_start=False, max_iter=10000)
cold_model.fit(X_train,y_train)
print(cold_model.coefs_, cold_model.intercepts_)
cold_model.fit(X_train,y_train)
print(cold_model.coefs_, cold_model.intercepts_)

[array([[-0.04595779],
       [ 0.00919602],
       [ 0.00347475],
       [-0.00763128],
       [ 0.23989295],
       [ 0.5130012 ],
       [ 0.59278955]])] [array([0.89936677])]
[array([[-0.75949183],
       [ 0.04861275],
       [-0.03188835],
       [-0.00909946],
       [ 0.39644745],
       [ 0.53561677],
       [ 1.26656764]])] [array([0.05829677])]


We do partial_fit with cold start and observe no change in the parameters as nothing is reset.

In [9]:
cold_model.partial_fit(X_train,y_train)
print(cold_model.coefs_, cold_model.intercepts_)

[array([[-0.7596341 ],
       [ 0.04846873],
       [-0.03190048],
       [-0.00918513],
       [ 0.3961202 ],
       [ 0.53545913],
       [ 1.26641392]])] [array([0.05808994])]


We can observe the slight change in parameters with warm start.

In [10]:
warm_model = sklearn.neural_network.MLPRegressor(hidden_layer_sizes=(), warm_start=True, max_iter=10000)
warm_model.fit(X_train,y_train)
print(warm_model.coefs_, warm_model.intercepts_)
warm_model.fit(X_train,y_train)
print(warm_model.coefs_, warm_model.intercepts_)

[array([[ 0.23472605],
       [ 0.02534595],
       [ 0.04413377],
       [-0.01048141],
       [ 0.99828938],
       [ 0.32689782],
       [ 1.40256776]])] [array([1.27939597])]
[array([[ 0.23500473],
       [ 0.02563303],
       [ 0.04441742],
       [-0.01019369],
       [ 0.9965225 ],
       [ 0.32718517],
       [ 1.40078723]])] [array([1.27966795])]


In [11]:
warm_model.partial_fit(X_train,y_train)
print(warm_model.coefs_, warm_model.intercepts_)

[array([[ 0.23398246],
       [ 0.02463401],
       [ 0.04342073],
       [-0.01119203],
       [ 0.9953371 ],
       [ 0.32620675],
       [ 1.39966974]])] [array([1.27862898])]


## partial_fit with Passive Aggressive Regressor

As said in sklearn docs:
> The passive-aggressive algorithms are a family of algorithms for large-scale learning. They are similar to the Perceptron in that they do not require a learning rate. However, contrary to the Perceptron, they include a regularization parameter C.

The passive side of the algorithm keeps the model if the prediction is correct, and aggressive one changes the model if the prediction is incorrect.

# Split the data again

In [12]:
y = df["mpg"]
X = df.loc[:, df.columns != "mpg"]
X_train, X_test, y_train, y_test = train_test_split(X, y)


Fit PassiveAggressiveRegressor

In [13]:
from sklearn.linear_model import PassiveAggressiveRegressor
mse_list = []
reg = PassiveAggressiveRegressor()
reg.partial_fit(X_train, y_train)
first_pred = reg.predict(X_test)
print(f"MSE is: {sklearn.metrics.mean_squared_error(first_pred, y_test)}")

MSE is: 242.58051951172263


In [14]:
reg = PassiveAggressiveRegressor()
data = []
c_cold, c_warm = 0.1, 0.01
for i, x in X_train.iterrows():
    reg.partial_fit([x.values], [y_train[i]])
    data.append({
        'c0': reg.intercept_[0],
        'c1': reg.coef_.flatten()[0],
        'c2': reg.coef_.flatten()[1],
        'mse_test': np.mean((reg.predict(X_test.values) - y_test)**2),
        'i': i
    })
    if i == 20:
        reg.C = c_warm
df_stats = pd.DataFrame(data)

In [15]:
df_stats

c0        c1        c2     mse_test    i
0    0.000001  0.000012  0.000443   224.463539    0
1    0.000003  0.000018  0.000598   240.792368  108
2    0.000005  0.000024  0.000753   531.940399  352
3    0.000005  0.000026  0.000788   627.109381  167
4    0.000003  0.000017  0.000501   226.493117   60
..        ...       ...       ...          ...  ...
289  0.000132 -0.000018 -0.020651   261.402379  214
290  0.000135 -0.000005 -0.020280   333.857844  183
291  0.000135 -0.000007 -0.020347   255.845520  340
292  0.000134 -0.000009 -0.020401   209.395166  234
293  0.000138  0.000007 -0.020044  1102.661045  349

[294 rows x 5 columns]

## Hosting our model
We will use skops library that lets us push our models to Hugging Face Hub! It saves the model, generates a config file including the configs to reproduce the experiment and more! (Model cards including feature importances, model hyperparameters, metrics and plots coming very soon 🤩)

**I ran this notebook on my local because skops follows PyData stack (scikit-learn & friends) which supports python3.8, so I uploaded the model [here](https://huggingface.co./merve/passive-agressive-regressor) through my local 🙂**

Hugging Face Hub needs a token for authentication, I will pass the token through getpass.

In [16]:
from getpass import getpass
token = getpass(f"Pass the Hub token:")

Pass the Hub token: ·····································


We will now save this model, use skops to initialize a Hugging Face Hub repository, let it create a configuration file to reproduce our experiment, serialize the model to repository and push it to Hub!

In [19]:
from skops import hub_utils
from tempfile import mkstemp, mkdtemp
import os
import pickle

# save the model to a temporary directory
_, pkl_name = mkstemp(prefix="skops")
with open(pkl_name, mode="bw") as f:
    pickle.dump(reg, file=f)

# initialize the repository 
local_repo = mkdtemp(prefix="skops")
hub_utils.init(model=pkl_name, 
               task="tabular-regression",
               requirements=["scikit-learn"], 
               dst=local_repo,
               data=X_train)

# see what's inside the repository
print(os.listdir(local_repo))

['config.json', 'skops47mqlzp0']


Currently in the repository there's model file and `config.json` that contains task type, example data, requirements and more. These are useful to enable inference API on 🤗Hub. 
We will now add a model card.

In [24]:
from skops import card
from pathlib import Path
# I will pass the model and metadata from config file
model_card = card.Card(reg, metadata=card.metadata_from_config(Path(local_repo)))

Let's some information to our card.

In [25]:
link = "https://www.kaggle.com/code/unofficialmerve/incremental-online-training-with-scikit-learn/"
description = f"This is a passive-agressive regression model used for continuous training. Find the notebook [here]({link})"
limitations = "This model is not ready to be used in production. It's trained to predict MPG a car spends based on it's attributes."
model_card.add(model_description=description,
              limitations=limitations,
              )

Card(
  model=PassiveAggressiveRegressor(C=0.01),
  metadata.library_name=sklearn,
  metadata.tags=['sklearn', 'skops', 'tabular-regression'],
  metadata.model_file=skops47mqlzp0,
  metadata.widget={...},
  model_description='This is a passiv...online-training-with-scikit-learn/)',
  limitations="This model is not read...r spends based on it\'s attributes.",
)

We can now save the model card to the local repository.

In [29]:
model_card.save(Path(local_repo) / "README.md")

*Let's push the model to 🤗Hub!*

In [30]:
# Push to Hub!
from skops import hub_utils
hub_utils.push(
    repo_id="scikit-learn/passive-agressive-regressor",
    source=local_repo,
    token=token,
    create_remote=True
)
# create_remote creates a remote repository if it doesn't exist

You can find the model [here](https://huggingface.co./scikit-learn/passive-agressive-regressor). We will soon introduce automatic creation of model cards. 🙂

# References
- [This stackoverflow discussion](https://stackoverflow.com/questions/38052342/what-is-the-difference-between-partial-fit-and-warm-start) is full of helpful answers.
- Sklearn docs on [PassiveAggressiveRegressor](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.PassiveAggressiveRegressor.html)
- I got a lot of help from [calmcode's chapter on partial_fit](https://calmcode.io/partial_fit/introduction.html). 🙂
- See [skops](https://github.com/skops-dev/skops/) here and watch for new features we're adding!